In [1]:
import os
import numpy as np
import pandas as pd
from ast import literal_eval
from tqdm import tqdm
import random
import tensorflow as tf
import re
import matplotlib
from matplotlib import pyplot as plt
import sys
import copy
matplotlib.rcParams['pdf.fonttype'] = 42
matplotlib.rcParams['ps.fonttype'] = 42

import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Conv2D, Dropout, Flatten, MaxPooling2D
#from tensorflow.python.ops.numpy_ops import np_config
#np_config.enable_numpy_behavior()
from tensorflow.keras.regularizers import l2
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.layers import Embedding, LSTM, Dense, Dropout, InputLayer, Reshape
from sklearn.metrics import roc_curve, auc, average_precision_score, matthews_corrcoef, f1_score, precision_score


In [2]:
#Put in master excel sheet from Sugiyama et al. 
excel = '41598_2019_46385_MOESM3_ESM.xlsx'
file_name = 'UP000005640_9606.txt' #Reference proteome
df = pd.read_csv(file_name, sep='delimiter', header=None)

C:\Users\Clair\AppData\Local\Temp\ipykernel_19376\619119312.py:4: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  df = pd.read_csv(file_name, sep='delimiter', header=None)


In [3]:
#Load all possible Uniprot IDs from reference proteome
df.fillna("NA", inplace=True) # just in case any "NA" got turned into NaNs
ID_df = df[df[0].str.contains(">")][0]
ID_list = []
for i in range(len(ID_df)):  #This dataset uses a different Uniprot form than previous so select it differently
    long=ID_df.iloc[i].split("|")[2]
    ID_list.append(long.split(" ")[0])
ID_array = np.array(ID_list)
print("ID array has been made!")

#Makes array of sequences
sequences = []
indices_of_uniprot_ids = list(df[df[0].str.contains(">")].index)
for i in range(len(indices_of_uniprot_ids)-1):
    # concatenate all into one string
    sequences.append(df[indices_of_uniprot_ids[i]+1:indices_of_uniprot_ids[i+1]][0].sum())
    if i == len(indices_of_uniprot_ids)-2:
        sequences.append(df[indices_of_uniprot_ids[i+1]+1:][0].sum())
sequences = np.array(sequences)
print("Lines have been separated!")

# Creates dictionary that maps Uniprot ID to sequence
pairs = zip(ID_array, sequences)
protein_dict = {A:B for A,B in pairs}
print("protein_dict has been made!")

ID array has been made!
Lines have been separated!
protein_dict has been made!


In [4]:
#Load excel sheet
sheet = pd.read_excel(excel)
Data=sheet[["Kinase", "Uniprot ID", "Position"]]

Kinase=Data.iloc[:, 0] 
Kinase=Kinase.to_numpy(dtype=str)

ID=Data.iloc[:, 1] 
ID=ID.to_numpy(dtype=str)

Position=Data.iloc[:, 2] 
Position=Position.to_numpy(dtype=str)

In [16]:
#Learn things about the dataset
#How many kinases
Unique_kinases=np.unique(Kinase)
print(Unique_kinases.size)
print(Unique_kinases)

#Make sure have correct ID form
print(ID_array[300])

386
['ABL1' 'ABL1[E255K]' 'ABL1[T315I]' 'ABL2' 'ACK' 'ACTR2' 'ACTR2B' 'AKT1'
 'AKT2' 'AKT3' 'ALK' 'ALK1' 'ALK2' 'ALK4' 'ALK[F1174L]' 'ALK[R1275Q]'
 'AMPKa1/b1/g1' 'AMPKa2/b1/g1' 'AXL' 'AurA' 'AurB' 'AurC' 'BARK1' 'BARK2'
 'BLK' 'BMPR1A' 'BMPR1B' 'BMPR2' 'BMX' 'BRAF' 'BRAF[V600E]' 'BRK' 'BRSK1'
 'BRSK2' 'BTK' 'BUB1' 'BUBR1' 'CAMKK1' 'CAMKK2' 'CDC2/CycB1' 'CDC7/ASK'
 'CDK11/CycC' 'CDK2/CycA2' 'CDK2/cycE1' 'CDK3/CycE1' 'CDK4/CYclin D1'
 'CDK4/CycD3' 'CDK5/p25' 'CDK6/CycD3' 'CDK6/Cyclin D1' 'CDK7/CycH/MAT1'
 'CDK8/CycC' 'CDK9/CycT1' 'CDK9/Cyclin K' 'CGK2' 'CHK1' 'CHK2' 'CK1a'
 'CK1d' 'CK1e' 'CK1g1' 'CK1g2' 'CK1g3' 'CK2a1' 'CK2a2' 'CLK1' 'CLK2'
 'CLK3' 'CLK4' 'COT' 'CRIK' 'CRK7/cycL1' 'CSK' 'CTK' 'CaMK1a' 'CaMK1b'
 'CaMK1d' 'CaMK2a' 'CaMK2b' 'CaMK2d' 'CaMK2g' 'CaMK4' 'DAPK1' 'DAPK2'
 'DAPK3' 'DCLK1' 'DCLK2' 'DDR1' 'DDR2' 'DLK' 'DMPK1' 'DRAK2' 'DYRK1A'
 'DYRK1B' 'DYRK2' 'DYRK3' 'DYRK4' 'EEF2K' 'EGFR' 'EGFR[L858R]'
 'EGFR[L861Q]' 'EGFR[T790M/L858R]' 'EGFR[T790M]' 'EPHA1' 'EPHA2' 'EPHA3'
 'EPH

In [5]:
def above_threshold (kinases, threshold, kinase_split):
    """
    Returns number of kinases that have the number of sites over a given threshold
    """
    ticker=0
    IDs=[]
    for i in kinases:
        subarray=np.where(Kinase == i, 1, 0)
        sum=np.sum(subarray)
        #print (sum)
        if sum > threshold:
            ticker +=1
            IDs.append(i)
    print (ticker)
    return IDs

def remove_slash (dataset):
    new_dataset=[]
    for i in dataset:
        if '/' in i:
            new = i.replace("/", "_")
            new_dataset.append(new)
        else:
            new=i
            new_dataset.append(new)
    new_dataset=np.array(new_dataset)
    return new_dataset

def create_datasets (kinases, kinase_split, ID_split, Position_split, folder):
    """

    """
    kinase_split=remove_slash(kinase_split)
    for i in kinases:
        #print (i)
        idx=np.where(kinase_split==i)[0]
        #print (idx)
        sub_kinase=kinase_split[idx[0]:idx[-1]+1]
        sub_ID=ID_split[idx[0]:idx[-1]+1]
        sub_position=Position_split[idx[0]:idx[-1]+1]
        stacked=np.stack((sub_kinase, sub_ID, sub_position))
        np.save(f'{folder}/{str(i)}', stacked)

        print(sub_position)

In [18]:
over_1000=above_threshold (Unique_kinases, 1000, Kinase)
over_500=above_threshold (Unique_kinases, 500, Kinase)

over_1000=remove_slash(over_1000)
over_500=remove_slash(over_500)

#print (Kinase)
create_datasets(over_500, Kinase, ID, Position, "Kinase Datasets")

67
159
['S212' 'Y151' 'Y21' ... 'Y107' 'Y1165' 'Y669']
['Y151' 'Y21' 'Y213' ... 'Y107' 'S117' 'Y1165']
['Y151' 'Y21' 'Y50' ... 'Y1007' 'S120' 'Y124']
['Y106' 'Y151' 'Y213' ... 'Y72' 'Y107' 'Y669']
['S212' 'S47' 'Y106' ... 'Y1355' 'Y669' 'Y167']
['Y21' 'Y213' 'Y50' ... 'Y97' 'Y1569' 'Y167']
['S212' 'S47' 'Y21' ... 'Y107' 'Y114' 'Y167']
['Y21' 'Y50' 'Y121' ... 'Y1569' 'Y1066' 'Y167']
['S148' 'S145' 'T141' 'S134' 'S513' 'S518' 'S521' 'S598' 'Y594' 'S1762'
 'S455' 'S54' 'Y55' 'S368' 'S199' 'S368' 'S52' 'Y53' 'S54' 'Y55' 'S199'
 'S368' 'S52' 'Y53' 'S53' 'Y54' 'S54' 'Y55' 'S331' 'S100' 'S124' 'S17'
 'S176' 'S336' 'S36' 'S39' 'S46' 'S17' 'S176' 'S45' 'S135' 'S137' 'S242'
 'S104' 'S134' 'S173' 'S201' 'S184' 'T10' 'S658' 'S129' 'Y92' 'Y58' 'S246'
 'S279' 'S320' 'S350' 'S490' 'S870' 'S401' 'S52' 'S78' 'S80' 'S125' 'S261'
 'S44' 'Y106' 'S362' 'S474' 'S192' 'S123' 'S71' 'S398' 'S453' 'T422'
 'S147' 'S576' 'S751' 'Y754' 'S211' 'S27' 'S31' 'S331' 'S585' 'S65' 'S162'
 'S99' 'S759' 'S898' 'T900' 'S612

In [6]:
#Now let's do some checks on the datasets

def S_T_Y (dataset_file, folder="Kinase Datasets"):
    """
    Checks the ratio of S, T, and Y sites in a dataset
    """
    dataset=np.load(f'{folder}/{dataset_file}', allow_pickle=True)
    sites=dataset[2, :]
    print (sites)
    S=0
    T=0
    Y=0
    for i in sites:
        if 'S' in i:
            S+=1
        elif 'T' in i:
            T+=1
        elif 'Y' in i:
            Y+=1
    print ("S="+str(S))
    print ("T="+str(T))
    print ("Y="+str(Y))
    print ("Total sites="+str(len(sites)))
    if S+T > Y:
        return "S/T kinase"
    else:
        return "Y kinase"


def S_T_datasets (kinase_list, folder="Kinase Datasets"):
    """
    Specifies which kinases are S/T kinases
    """
    S_T_kinase=[]
    for i in kinase_list:
        dataset=str(i)+'.npy'
        if S_T_Y(dataset) == "S/T kinase":
            S_T_kinase.append(i)
    return S_T_kinase

over_500_S_T= S_T_datasets (over_500)
np.save("over_500_S_T", over_500_S_T)

NameError: name 'over_500' is not defined

In [10]:
#Now let's make a bunch of functions
def remove_Y_sites (dataset_file, folder="Kinase Datasets"):
    """
    Removes Y sites

    """
    dataset=np.load(f'{folder}/{dataset_file}', allow_pickle=True)
    sites=dataset[2, :]
    to_delete=np.zeros(len(sites), dtype=bool)
    for i in range (0, len(sites)):
        if "Y" in sites[i]:
            to_delete[i]=True
    copy=np.delete(dataset, to_delete, axis=1)        
    #print (len(copy[0, :]))
    return (copy)

def ndtolot (ndarray):
    """
    converts 2D ndarray (n, 2) to a list of tuples
    """
    list=[]
    for i in range (0, len(ndarray[:, 0])):
        holding=(ndarray[i, 0], int(ndarray[i, 1]))
        list.append(holding)
    return list

def make_pos_kmers (dataset_file, protein_dict, Site="ST", folder="Kinase Datasets", k=53):
    """
    Makes kmers from a list of positive sites
    Site is given in bio notation (not python) which starts at 1 and is a string with the identity of the amino acid (S/T/Y)
    """
    dataset=np.load(f'{folder}/{dataset_file}', allow_pickle=True)
    kmers=[]
    S_site_array=[]
    T_site_array=[]
    half=int((k-1)/2)
    if Site=="ST":
        dataset=remove_Y_sites (dataset_file, folder=folder)
        sites=dataset[2, :]
        for i in range(0, len(sites)):
            ID=dataset[1, i]
            location=int(sites[i].replace("S","").replace("T",""))
            try:
                seq=protein_dict[ID]
                if location <= half: #To deal with sites near the n terminus
                    if location > len(seq)-half: #To deal with sequences shorter than k
                        gap="-"*(half-location+1)
                        gap2="-"*int(half-(len(seq)-location))
                        kmer=seq[0 : int(location+half)]
                        kmer=gap+kmer+gap2
                    else: 
                        gap="-"*(half-location+1)
                        kmer=seq[0 : int(location+half)]
                        kmer=gap+kmer
                elif location > len(seq)-half: #To deal with sites near the C terminus
                    gap="-"*int(half-(len(seq)-location))
                    kmer=seq[int(location-half-1): len(seq)]
                    kmer=kmer+gap
                else:
                    kmer=seq[int(location-half-1): int(location+half)]

                if location > len(seq): #Will not add to list of kmers
                    print ("Site outside of seq bounds, site: "+str(location)+", sequnce length: "+str(len(seq)))
                    print (ID)
                elif seq[int(location-1)] == "S" or seq[int(location-1)]=="@":
                    S_site_array.append ((ID, location))
                    kmers.append(kmer)
                elif seq[int(location-1)] == "T" or seq[int(location-1)]=="&":
                    T_site_array.append ((ID, location))
                    kmers.append(kmer)
                else:
                    print(seq[int(location-1)])
                    print ("Sequence key error for "+ID+" at " + str(location)) #Will not add it to list of kmers because doesn't match uniprot
                    #raise Exception("Sequence key error for "+ID+" at " + str(location))
                if len(kmer) != k:
                    print (kmer)
                    print (len(kmer))            
            except KeyError:
               print(ID+" not in protein_dict")    
    elif Site=="Y":
        print("Y not supported yet")
    else:
        raise Exception("Site name incorrect, please put ST or Y")

    print (len(kmers))
    return kmers, S_site_array, T_site_array

#kmers, site_array=make_pos_kmers ("ABL1.npy", protein_dict)
#print (site_array)

def make_full_dataset (dataset_file, protein_dict, Site="ST", folder="Kinase Datasets", k=53):
    """
    """
    pos_kmers, S_sites, T_sites = make_pos_kmers (dataset_file, protein_dict)
    if Site=="ST":
        s=len(S_sites)
        t=len(T_sites)
        
        ns=ndtolot(np.load('All_S_sites.npy', allow_pickle=True))
        nt=ndtolot(np.load('All_T_sites.npy', allow_pickle=True))

        for i in S_sites:
            ns.remove(i)
        
        for i in T_sites:
            nt.remove(i)
        
        neg_S_sites= random.sample(ns, s)
        neg_T_sites= random.sample(nt, t)
        neg_sites=neg_S_sites+ neg_T_sites
        print (len(neg_sites))
        
        #Now that we have the sites we need to make kmers
        neg_kmers=[]
        half=int((k-1)/2)
        for i in neg_sites:
            location=i[1]
            ID=i[0]
            #print (location)
            seq=protein_dict[ID]
            if location <= half:
                if location > len(seq)-half:
                    gap="-"*(half-location+1)
                    gap2="-"*int(half-(len(seq)-location))
                    kmer=seq[0 : int(location+half)]
                    kmer=gap+kmer+gap2
                else:
                    gap="-"*(half-location+1)
                    kmer=seq[0 : int(location+half)]
                    kmer=gap+kmer
                    #print (len(kmer))
            elif location > len(seq)-half:
                gap="-"*int(half-(len(seq)-location))
                #print (len(gap))
                kmer=seq[int(location-half-1): len(seq)]
                kmer=kmer+gap
            else:
                kmer=seq[int(location-half-1): int(location+half)]
            neg_kmers.append(kmer)

    elif Site=="Y":
        print("Y not supported yet")
    else:
        raise Exception("Site name incorrect, please put ST or Y")
    return pos_kmers, neg_kmers

#pos_kmers, neg_kmers=make_full_dataset ("ABL1.npy", protein_dict)
#print (neg_kmers)

In [145]:
#Make negative index dataset of S and Ts
#Let's put every site in an array with its Uniprot ID and site index (bio counting not python which starts at zero)
S_list=[]
T_list=[]
for key in protein_dict:
    #print (key)
    seq=protein_dict[key]
    for match in re.finditer("S", seq):
        S_list.append((key, match.start()+1))
        #print (match.start()+1)

print ("Number of S sites: "+str(len(S_list)))
np.save('All_S_sites', S_list)
print ("S sites saved")

for key in protein_dict:
    #print (key)
    seq=protein_dict[key]
    for matchT in re.finditer("T", seq):
        T_list.append((key, matchT.start()+1))
        #print (matchT.start()+1)

print ("Number of T sites: "+str(len(T_list)))
np.save('All_T_sites', T_list)
print ("T sites saved")

Number of S sites: 950789
S sites saved
Number of T sites: 610372
T sites saved


In [13]:
#Now let's make the labeled datasets and tensors
def labeling (dataset_file, protein_dict, k=53):
    """
    """
    kmers, S_sites, T_sites = make_pos_kmers(dataset_file, protein_dict, k=k)
    lprotein_dict=copy.deepcopy(protein_dict)
    for i in S_sites:
        ID=i[0]
        location=i[1]-1 #To turn to python index
        seq=lprotein_dict[ID]
        if seq[location]=="S":
            newseq= seq[:location] + "@" + seq[location + 1:]
        elif seq[location]=="@":
            print ("Already labeled")
        else:
            print (seq[location])
            raise Exception("Index error, no S")
        lprotein_dict[ID]=newseq
    for i in T_sites:
        ID=i[0]
        location=i[1]-1
        seq=lprotein_dict[ID]
        if seq[location]=="T":
            newseq= seq[:location] + "&" + seq[location + 1:]
        elif seq[location]=="&":
            print ("Already labeled")
        else:
            raise Exception("Index error, no T")
        lprotein_dict[ID]=newseq
    
    lpos_kmers0, lneg_kmers = make_full_dataset (dataset_file, lprotein_dict, k=k)
    #Now we need to revert central @ and & to S and T
    lpos_kmers=[]
    half=int((k-1)/2)
    #print (lpos_kmers0)
    for kmer in lpos_kmers0:
        #print (kmer)
        if kmer[half]=="@":
            rkmer=kmer[:half] + "S" + kmer[half+1:]
        elif kmer[half]=="&":
            rkmer=kmer[:half] + "T" + kmer[half+1:]
        else:
            raise Exception("Incorrect value at kmer center, here is the kmer:"+kmer)
        lpos_kmers.append(rkmer)
    #Don't need to remove central @ and & for negatives becuase they shouldn't be there!
    return lpos_kmers, lneg_kmers


#lpos_kmers, lneg_kmers=labeling("ABL1.npy", protein_dict)



alphabet_with_labels = "ARNDCEQGHILKMFPSTWYV@&-UX" #
alphabet_without_labels = "ARNDCEQGHILKMFPSTWYV-UX"

def convert_to_onehot(data, alphabet):
    #Creates a dict, that maps to every char of alphabet an unique int based on position
    global char_to_int
    char_to_int = dict((c,i) for i,c in enumerate(alphabet))
    encoded_data = []
    #Replaces every char in data with the mapped int
    encoded_data.extend([char_to_int[char] for char in data])
    return encoded_data

def tensor_encoding(x_data, depth, type, alphabet):
    indices = []
    t2 = []
    for i in tqdm(range(len(x_data))):
        indices.append(convert_to_onehot(x_data[i,0], alphabet))
        if len(convert_to_onehot(x_data[i,0], alphabet)) != 53:
            print (x_data[i,0])
            print ("Length off")
    array=np.stack(indices, axis=0)
    if type == 'emb':
        return array
    for i in tqdm(range(len(indices))):
        t1 = tf.one_hot(indices[i], depth) # output: [9 x 23]
        t2.append(t1)
    return t2

In [8]:
#Now let's throw it all together

def make_datasets_train_models (dataset_file, protein_dict, k=53, Site="ST", folder="Kinase Datasets", trial="Trial1"):
    """
    """
    pos_kmers, neg_kmers = make_full_dataset (dataset_file, protein_dict, Site="ST", folder="Kinase Datasets", k=53)
    lpos_kmers, lneg_kmers = labeling (dataset_file, protein_dict, k=53)
    if 1==1: #len(pos_kmers) != len(neg_kmers) != len(lpos_kmers) != len(lneg_kmers):
        print (len(pos_kmers))
        print (len(lpos_kmers))
        print (len(neg_kmers))
        print (len(lneg_kmers))
        #raise Exception ("Check kmer construction, not all are set equal")
    y_pos=np.ones((len(pos_kmers)), dtype=np.int32)
    y_neg=np.zeros((len(neg_kmers)), dtype=np.int32)

    pos_kmers=np.array(pos_kmers)
    neg_kmers=np.array(neg_kmers)
    lpos_kmers=np.array(lpos_kmers)
    lneg_kmers=np.array(lneg_kmers)
    
    pos_k = np.stack((pos_kmers, y_pos), axis=1)
    neg_k = np.stack((neg_kmers, y_neg), axis=1)
    lpos_k = np.stack((lpos_kmers, y_pos), axis=1)
    lneg_k = np.stack((lneg_kmers, y_neg), axis=1)

    #print (np.shape(pos_k))
    #print (np.shape(lpos_k))
    #print (np.shape(neg_k))
    #print (np.shape(lneg_k))

    full= np.vstack([pos_k,neg_k])
    lfull = np.vstack([lpos_k,lneg_k])
    np.random.shuffle(full)
    np.random.shuffle(lfull)

    print (full[:, 1].dtype)
    #print (np.shape(full))
    #print (np.shape(lfull))

    x_data, y_data = np.split(full, 2, axis=1)
    x_datal, y_datal = np.split(lfull, 2, axis=1)

    #print (np.shape(x_datal))
    y_data=y_data.astype(np.int32)
    y_datal=y_datal.astype(np.int32)
    #print (y_data.dtype)
    #print (y_data)

    # Split into train, validation, and test datasets
    N = len(full)
    x_train = x_data[0:int(0.8*N), :]
    #print (x_train)
    y_train = y_data[0:int(0.8*N)]
    #print (y_train)

    x_validation = x_data[int(0.8*N):int(0.8*N)+int(0.1*N), :]
    y_validation = y_data[int(0.8*N):int(0.8*N)+int(0.1*N)]

    x_test = x_data[int(0.8*N)+int(0.1*N):, :]
    y_test = y_data[int(0.8*N)+int(0.1*N):]

    x_trainl = x_datal[0:int(0.8*N), :]
    y_trainl = y_datal[0:int(0.8*N)]

    x_validationl = x_datal[int(0.8*N):int(0.8*N)+int(0.1*N), :]
    y_validationl = y_datal[int(0.8*N):int(0.8*N)+int(0.1*N)]

    x_testl = x_datal[int(0.8*N)+int(0.1*N):, :]
    y_testl = y_datal[int(0.8*N)+int(0.1*N):]

    #Make tensors of x data
    tensor1 = tensor_encoding(x_train, 23, 'emb', alphabet_without_labels)
    tensor2 = tensor_encoding(x_validation, 23, 'emb', alphabet_without_labels)
    tensor3 = tensor_encoding(x_test, 23, 'emb', alphabet_without_labels)
    tensor4 = tensor_encoding(x_trainl, 23, 'emb', alphabet_with_labels)
    tensor5 = tensor_encoding(x_validationl, 23, 'emb', alphabet_with_labels)
    tensor6 = tensor_encoding(x_testl, 23, 'emb', alphabet_with_labels)

    print (type(tensor1))
    print (tensor1.dtype)
    print (y_train.dtype)
    #print (np.shape(tensor2))
    #print (np.shape(tensor3))
    #print (np.shape(tensor4))
    #print (np.shape(tensor5))
    #print (np.shape(tensor6))

    directory = dataset_file.replace(".npy","")
    parent_dir = folder+'/'
    path = os.path.join(parent_dir, directory) 
    try:
        os.mkdir(path) 
    except:
        pass
    
    #Save datasets
    np.save(f'{path}/{trial}_x_train_without_labels', tensor1)
    np.save(f'{path}/{trial}_y_train_without_labels', y_train)
    np.save(f'{path}/{trial}_x_validation_without_labels', tensor2)
    np.save(f'{path}/{trial}_y_validation_without_labels', y_validation)
    np.save(f'{path}/{trial}_x_test_without_labels', tensor3)
    np.save(f'{path}/{trial}_y_test_without_labels', y_test)
    np.save(f'{path}/{trial}_x_train_with_labels', tensor4)
    np.save(f'{path}/{trial}_y_train_with_labels', y_trainl)
    np.save(f'{path}/{trial}_x_validation_with_labels', tensor5)
    np.save(f'{path}/{trial}_y_validation_with_labels', y_validationl)
    np.save(f'{path}/{trial}_x_test_with_labels', tensor6)
    np.save(f'{path}/{trial}_y_test_with_labels', y_testl)

    #Add the model
    callback = tf.keras.callbacks.EarlyStopping(monitor='val_loss', mode='min', verbose=1, patience=15, restore_best_weights=True)

    model = Sequential()
    model.add(Embedding(input_dim=256, output_dim=21, embeddings_initializer={'class_name': 'RandomUniform',
         'config': {'minval': -0.05, 'maxval': 0.05, 'seed': None}}, input_length=53, name="emb_layer"))
    model.add(Reshape((53, 21, 1), input_shape=(53, 21)))
    model.add(Conv2D(16, (3, 3), padding='valid', input_shape=(53, 21, 1), activation='relu', kernel_regularizer=l2(1e-06)))
    model.add(MaxPooling2D(pool_size=(2,2), padding='valid'))
    model.add(Flatten())
    model.add(Dense(32, activation="relu"))
    model.add(Dropout(0.1))
    model.add(Dense(1, activation='sigmoid'))
    model.summary()

    model.compile(optimizer=Adam(1e-03), 
                  loss='BinaryCrossentropy', 
                  metrics=['accuracy'])
    history = model.fit(x=tensor1,y=y_train,
              batch_size=100, epochs=400,
              validation_data=(tensor2, y_validation), 
              callbacks=[callback], verbose=1)
    model.save(f'{path}/{directory}_emb_CNN_no_labels_{trial}.h5')
    model.evaluate(tensor3, y_test)

     # The predictions are between 0 and 1 because of the sigmoid activation
    # function of the last layer in the NN
    pred = model.predict(tensor3).flatten()

    # We can also calculate the AUC to get an estimate how good the NN actually learned
    print ("Without labels")
    fpr, tpr, thresholds = roc_curve(y_test, pred)
    print("AUC:", round(auc(fpr, tpr), 4))
    print("AUPRC:", round(average_precision_score(y_test, pred), 4))
    pred2 = (pred > 0.5)
    pred2 = np.array(pred2)
    pred2 = pred2.astype(int)
    print("MCC:", round(matthews_corrcoef(y_test, pred2), 4))
    print("F1:", round(f1_score(y_test, pred2), 4))
    print("Sensitivity:", round(np.average(tpr), 4))
    print("Specificity:", round(np.average(1-fpr), 4))
    print("Precision:", round(precision_score(y_test, pred2), 4))

    #Now with labels
    historyl = model.fit(x=tensor4,y=y_trainl,
              batch_size=100, epochs=400,
              validation_data=(tensor5, y_validationl), 
              callbacks=[callback], verbose=1)
    model.save(f'{path}/{directory}_emb_CNN_with_labels_{trial}.h5')
    model.evaluate(tensor6, y_testl)

     # The predictions are between 0 and 1 because of the sigmoid activation
    # function of the last layer in the NN
    predl = model.predict(tensor6).flatten()

    # We can also calculate the AUC to get an estimate how good the NN actually learned
    print ("With labels")
    fprl, tprl, thresholdsl = roc_curve(y_testl, predl)
    print("AUC:", round(auc(fprl, tprl), 4))
    print("AUPRC:", round(average_precision_score(y_testl, predl), 4))
    pred2l = (predl > 0.5)
    pred2l = np.array(pred2l)
    pred2l = pred2l.astype(int)
    print("MCC:", round(matthews_corrcoef(y_testl, pred2l), 4))
    print("F1:", round(f1_score(y_testl, pred2l), 4))
    print("Sensitivity:", round(np.average(tprl), 4))
    print("Specificity:", round(np.average(1-fprl), 4))
    print("Precision:", round(precision_score(y_testl, pred2l), 4))

#make_datasets_train_models("ABL1.npy", protein_dict)

In [14]:
make_datasets_train_models ("p70S6K.npy", protein_dict, trial="Trial1")

BA2L2_HUMAN not in protein_dict
BA2L2_HUMAN not in protein_dict
BA2L2_HUMAN not in protein_dict
BA2L2_HUMAN not in protein_dict
BA2L2_HUMAN not in protein_dict
BAT2_HUMAN not in protein_dict
CJ047_HUMAN not in protein_dict
DBPA_HUMAN not in protein_dict
DBPA_HUMAN not in protein_dict
N
Sequence key error for DDX17_HUMAN at 492
G
Sequence key error for DDX17_HUMAN at 595
DHSA_HUMAN not in protein_dict
DHSA_HUMAN not in protein_dict
F175B_HUMAN not in protein_dict
F192A_HUMAN not in protein_dict
FA21A_HUMAN not in protein_dict
FA21B_HUMAN not in protein_dict
FA21C_HUMAN not in protein_dict
GRP78_HUMAN not in protein_dict
GRP78_HUMAN not in protein_dict
GRP78_HUMAN not in protein_dict
HN1_HUMAN not in protein_dict
HSP71_HUMAN not in protein_dict
IF2BL_HUMAN not in protein_dict
IF2BL_HUMAN not in protein_dict
IMA2_HUMAN not in protein_dict
K0528_HUMAN not in protein_dict
K0528_HUMAN not in protein_dict
K6PP_HUMAN not in protein_dict
K6PP_HUMAN not in protein_dict
E
Sequence key error for K

100%|███████████████████████████████████████████████████████████████████████████████| 97/97 [00:00<00:00, 32389.74it/s]


<class 'numpy.ndarray'>
int32
int32
Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 emb_layer (Embedding)       (None, 53, 21)            5376      
                                                                 
 reshape (Reshape)           (None, 53, 21, 1)         0         
                                                                 
 conv2d (Conv2D)             (None, 51, 19, 16)        160       
                                                                 
 max_pooling2d (MaxPooling2D  (None, 25, 9, 16)        0         
 )                                                               
                                                                 
 flatten (Flatten)           (None, 3600)              0         
                                                                 
 dense (Dense)               (None, 32)                115232    
                    

In [239]:
np.save("over_500_S_T", over_500_S_T)
for dataset in over_500_S_T:
    print (dataset)
    make_datasets_train_models (dataset+".npy", protein_dict, trial="Trial5")

AurA
D
Sequence key error for DDX17_HUMAN at 593
EAP1_HUMAN not in protein_dict
GRP78_HUMAN not in protein_dict
HSP71_HUMAN not in protein_dict
IMA2_HUMAN not in protein_dict
K6PP_HUMAN not in protein_dict
MLTK_HUMAN not in protein_dict
NCRP1_HUMAN not in protein_dict
NCRP1_HUMAN not in protein_dict
P
Sequence key error for NRDC_HUMAN at 320
NTKL_HUMAN not in protein_dict
PROSC_HUMAN not in protein_dict
PYR5_HUMAN not in protein_dict
PYR5_HUMAN not in protein_dict
SPTA2_HUMAN not in protein_dict
STK6_HUMAN not in protein_dict
STK6_HUMAN not in protein_dict
STK6_HUMAN not in protein_dict
STK6_HUMAN not in protein_dict
STK6_HUMAN not in protein_dict
STK6_HUMAN not in protein_dict
STK6_HUMAN not in protein_dict
SYG_HUMAN not in protein_dict
P
Sequence key error for USP9X_HUMAN at 639
477
477
D
Sequence key error for DDX17_HUMAN at 593
EAP1_HUMAN not in protein_dict
GRP78_HUMAN not in protein_dict
HSP71_HUMAN not in protein_dict
IMA2_HUMAN not in protein_dict
K6PP_HUMAN not in protein_dict

100%|██████████████████████████████████████████████████████████████████████████████████████████| 96/96 [00:00<?, ?it/s]

<class 'numpy.ndarray'>
int32
int32


Model: "sequential_297"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 emb_layer (Embedding)       (None, 53, 21)            5376      
                                                                 
 reshape_297 (Reshape)       (None, 53, 21, 1)         0         
                                                                 
 conv2d_297 (Conv2D)         (None, 51, 19, 16)        160       
                                                                 
 max_pooling2d_297 (MaxPooli  (None, 25, 9, 16)        0         
 ng2D)                                                           
                                                                 
 flatten_297 (Flatten)       (None, 3600)              0         
                                                                 
 dense_594 (Dense)           (None, 32)                115232    
                                                    

100%|████████████████████████████████████████████████████████████████████████████████████████| 114/114 [00:00<?, ?it/s]


...

100%|█████████████████████████████████████████████████████████████████████████████| 132/132 [00:00<00:00, 33008.29it/s]


<class 'numpy.ndarray'>
int32
int32
Model: "sequential_364"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 emb_layer (Embedding)       (None, 53, 21)            5376      
                                                                 
 reshape_364 (Reshape)       (None, 53, 21, 1)         0         
                                                                 
 conv2d_364 (Conv2D)         (None, 51, 19, 16)        160       
                                                                 
 max_pooling2d_364 (MaxPooli  (None, 25, 9, 16)        0         
 ng2D)                                                           
                                                                 
 flatten_364 (Flatten)       (None, 3600)              0         
                                                                 
 dense_728 (Dense)           (None, 32)                115232    
                

100%|███████████████████████████████████████████████████████████████████████████████| 97/97 [00:00<00:00, 19400.48it/s]

<class 'numpy.ndarray'>
int32
int32


Model: "sequential_365"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 emb_layer (Embedding)       (None, 53, 21)            5376      
                                                                 
 reshape_365 (Reshape)       (None, 53, 21, 1)         0         
                                                                 
 conv2d_365 (Conv2D)         (None, 51, 19, 16)        160       
                                                                 
 max_pooling2d_365 (MaxPooli  (None, 25, 9, 16)        0         
 ng2D)                                                           
                                                                 
 flatten_365 (Flatten)       (None, 3600)              0         
                                                                 
 dense_730 (Dense)           (None, 32)                115232    
                                                    

In [8]:
def frequency(k, kmers, model):
    """

    Parameters
    ----------
    k : int
        an odd number that specifies that length of the kmer with the
        phosphorylation site in the middle
    kmer : 2D array
        1D array with kmers

    Returns
    -------
    frequencies : 2D array
        2D array with columns distance away from center kmer PTM and 
        frequency of nearby PTMS

    """
    around_ind = k//2
    x=0
    z=0
    frequencies = {}
    for i in range(0, len(kmers)):
        if "@" in kmers[i]:
            x+=1
        elif "&" in kmers[i]:
            z+=1
        temp = kmers[i][around_ind+1:]
        for j in range(len(temp)):
            if "@" == temp[j]:
                if j+1 in frequencies.keys():
                    frequencies[j+1] += 1
                else:
                    frequencies[j+1] = 1
            elif "&" ==temp[j]:
                if j+1 in frequencies.keys():
                    frequencies[j+1] += 1
                else:
                    frequencies[j+1] = 1        
        
    
    frequencies = list(frequencies.items())
    frequencies = np.array(frequencies)
    print (frequencies)
    frequencies = frequencies[frequencies[:,0].argsort()]

    plt.figure(0)
    plt.bar(frequencies[:,0], frequencies[:,1])
    plt.xticks(frequencies[:,0])
    plt.title("Frequency of nearby PTM sites")
    plt.ylabel("Frequency amount")
    plt.xlabel("Distance to the right of k-mer center")
    plt.savefig("Kinase datasets/_Frequencies/"+model+"_frequencies.pdf", transparent=True)
    plt.show()

    return frequencies




In [19]:
over_500_S_T=np.load("over_500_S_T.npy", allow_pickle=True)
for dataset in over_500_S_T:
    print (dataset)
    pos_kmers, neg_kmers = labeling (dataset+".npy", protein_dict)
    #frequency(53, pos_kmers, dataset)
    print (pos_kmers)
    pos_kmers=np.asarray(pos_kmers,  dtype=str)
    np.savetxt("Kinase datasets/_labeled_kmer_sets/"+dataset+"_labeled_kmers.csv", pos_kmers, delimiter=",", fmt='%s')

AurA
D
Sequence key error for DDX17_HUMAN at 593
EAP1_HUMAN not in protein_dict
GRP78_HUMAN not in protein_dict
HSP71_HUMAN not in protein_dict
IMA2_HUMAN not in protein_dict
K6PP_HUMAN not in protein_dict
MLTK_HUMAN not in protein_dict
NCRP1_HUMAN not in protein_dict
NCRP1_HUMAN not in protein_dict
P
Sequence key error for NRDC_HUMAN at 320
NTKL_HUMAN not in protein_dict
PROSC_HUMAN not in protein_dict
PYR5_HUMAN not in protein_dict
PYR5_HUMAN not in protein_dict
SPTA2_HUMAN not in protein_dict
STK6_HUMAN not in protein_dict
STK6_HUMAN not in protein_dict
STK6_HUMAN not in protein_dict
STK6_HUMAN not in protein_dict
STK6_HUMAN not in protein_dict
STK6_HUMAN not in protein_dict
STK6_HUMAN not in protein_dict
SYG_HUMAN not in protein_dict
P
Sequence key error for USP9X_HUMAN at 639
477
D
Sequence key error for DDX17_HUMAN at 593
EAP1_HUMAN not in protein_dict
GRP78_HUMAN not in protein_dict
HSP71_HUMAN not in protein_dict
IMA2_HUMAN not in protein_dict
K6PP_HUMAN not in protein_dict
MLT